In [1]:
import os
import time
import subprocess

import numpy as np
import scipy.signal
import pandas as pd
import scipy.stats

from tvb.simulator.lab import *
from mne import time_frequency, filter
import plotly.graph_objects as go  # for data visualisation
import plotly.io as pio
from toolbox import timeseriesPlot, FFTplot, FFTpeaks, AEC, PLV, PLI, epochingTool, paramSpace

2020-12-15 22:49:24,352 - WARNING - tvb.simulator.common - psutil module not available: no warnings will be issued when a
    simulation may require more memory than available
   INFO  log level set to INFO


c:\users\f_r_e\pycharmprojects\brainmodels\venv\lib\site-packages\tvb\datatypes\surfaces.py:61: UserWarning: Geodesic distance module is unavailable; some functionality for surfaces will be unavailable.
  warnings.warn(msg)


In [2]:
# This simulation will generate FC for a virtual "Subject".
# Define identifier (i.e. could be 0,1,11,12,...)
subjectid = ".1973WilsonCowan"
main_folder="C:\\Users\\F_r_e\\PycharmProjects\\brainModels\\"+subjectid
ctb_folder="C:\\Users\\F_r_e\\PycharmProjects\\brainModels\\CTB_data\\output\\"
if subjectid not in os.listdir(ctb_folder):
    os.mkdir(ctb_folder+subjectid)
    os.mkdir(main_folder)

emp_subj = "subj04"

# Prepare bimodality test (i.e. Hartigans' dip test in an external R script via python subprocess
# Build subprocess command: [Rscript, script]
# cmd = ['C:\\Program Files\\R\\R-3.6.1\\bin\\Rscript.exe',
#        'C:\\Users\\F_r_e\\PycharmProjects\\brainModels\\diptest\\diptest.R']

simLength = 4100 # ms - relatively long simulation to be able to check for power distribution
samplingFreq = 1000 #Hz
transient=100 # ms to exclude from timeseries due to initial transient

# integrator: dt=T(ms)=1000/samplingFreq(kHz)=1/samplingFreq(HZ)
# integrator = integrators.HeunStochastic(dt=1000/samplingFreq, noise=noise.Additive(nsig=np.array([5e-6])))
integrator = integrators.HeunDeterministic(dt=1000/samplingFreq)

conn = connectivity.Connectivity.from_file(
    "C:\\Users\\F_r_e\\PycharmProjects\\brainModels\\CTB_data\\output\\CTB_connx66_"+emp_subj+".zip")
conn.weights = conn.scaled_weights(mode="tract")

mon = (monitors.Raw(),)

WARNING  File 'average_orientations' not found in ZIP.
WARNING  File 'cortical' not found in ZIP.
WARNING  File 'hemispheres' not found in ZIP.
WARNING  File 'areas' not found in ZIP.


Model parameters and coupling factor

In [3]:
m = models.WilsonCowan(P=np.array([0.31]),
                       
                   c_ee=np.array([3.25]), c_ei=np.array([2.5]), c_ie=np.array([3.75]), c_ii=np.array([0]),
                   alpha_e=np.array([1]), alpha_i=np.array([1]),

                   r_e=np.array([0]), r_i=np.array([0]), k_e=np.array([1]), k_i=np.array([1]),
                   tau_e=np.array([10]), tau_i=np.array([20]), theta_e=np.array([0]), theta_i=np.array([0]),

                   a_e=np.array([4]), a_i=np.array([4]), b_e=np.array([1]), b_i=np.array([1]),
                   c_e=np.array([1]), c_i=np.array([1]))


coup = coupling.Linear(a=np.array([0.5]))

In [4]:
tic0=time.time()
# Run simulation
sim = simulator.Simulator(model=m, connectivity=conn, coupling=coup,  integrator=integrator, monitors=mon)
sim.configure()

output = sim.run(simulation_length=simLength)
print("Simulation time: %0.2f sec" % (time.time() - tic0,))
# Extract data cutting initial transient
raw_data = output[0][1][transient:, 0, :, 0].T
raw_time = output[0][0][transient:]
regionLabels = conn.region_labels
regionLabels=list(regionLabels)
regionLabels.insert(0,"AVG")
# average signals to obtain mean signal frequency peak
data = np.asarray([np.average(raw_data, axis=0)])
data = np.concatenate((data, raw_data), axis=0)  # concatenate mean signal: data[0]; with raw_data: data[1:end]
# Check initial transient and cut data
timeseriesPlot(data[0:10], raw_time, regionLabels[0:10], main_folder, True)

Simulation time: 2.91 sec


In [5]:
# Fourier Analysis plot
FFTplot(data, simLength, regionLabels, main_folder, True)

fft_peaks = FFTpeaks(data, simLength - transient)[:, 0]